In [1]:
import openai
import json
import os
from sympy import symbols, Symbol

openai.api_key = open("/home/mcwave/code/automath/openai_api_key.txt").readline().strip()
#print(openai.api_key)

def convertToSympyWithGPT(prompt):
    messages = [{"role": "user", "content": "Convert to Sympy with a symbol and an expression: $" + prompt + '$'}]
    response = openai.ChatCompletion.create(
        model="gpt-3.5-turbo-1106",
        messages=messages,
        timeout=10
    )
    response_message = response["choices"][0]["message"]
    return response_message


def convertToSympy(prompt):
    response = convertToSympyWithGPT(prompt)["content"]
    #print(response)
    lcls = locals()
    if 't' in lcls:
        del t
    if 'expression' in lcls:
        del expression
    if 'expr' in lcls:
        del expr
    #
    lines = response.split('\n')
    #print(lines)
    for line in lines:
        exec(line, globals(), lcls)
    #
    output = None
    if "expression" in lcls:
        output = lcls["expression"]
    elif "expr" in lcls:
        output = lcls["expr"]
    #
    return lcls["t"], output

def convertToSympyWithRetry(prompt, retry=3):
    success = False
    for i in range(retry):
        try:
            sbl, expr = convertToSympy(prompt)
            success = True
        except:
            continue
        if sbl is None or expr is None:
            continue
        break
    if success:
        return sbl, expr
    else:
        return None, None

convertToSympyWithRetry('tan (7-7 t)') #'-\frac{3150 t^2-10920 t+9437}{3 \sqrt{3}}') #'-\\frac{17 t^2}{8}+\\frac{255 t}{2}-1906')

(t, -tan(7*t - 7))

In [2]:
def extract_equations(s):
    in_equation = False
    cur_equation = ""
    equations = []
    for i in range(len(s)):
        if s[i]=='$':
            in_equation = not in_equation
            if not in_equation:
                if len(cur_equation) > 0:
                    if ',' in cur_equation:
                        cur_equations = cur_equation.split(',')
                        for e in cur_equations:
                            equations.append(e.strip())
                    else:
                        equations.append(cur_equation)
                    cur_equation = ""
        elif in_equation:
            cur_equation += s[i]
    return equations
                
def parse_parametric_equations(path):
    fin = open(path, 'r')
    lines = fin.readlines()
    fin.close()
    line = ' '.join(lines)
    eqts = extract_equations(line)
    print(eqts)
    f_t, g_t, g_f_t = None, None, None
    for eqt in eqts:
        if len(eqt) <= 10:
            continue
        if eqt.startswith('x(t)'):
            f_t = eqt[eqt.find('=') + 1:]
        elif eqt.startswith('y(t)'):
            g_f_t = eqt[eqt.find('=') + 1:]
        elif eqt.startswith('y=') or eqt.startswith('y ='):
            g_t = eqt[eqt.find('=') + 1:]
            g_t = g_t.replace('x', 't')
    return f_t, g_t, g_f_t

def parse_function_evaluation(path):
    fin = open(path, 'r')
    lines = fin.readlines()
    fin.close()
    line = ' '.join(lines)
    eqts = extract_equations(line)
    eqt = eqts[0]
    if eqt.startswith('f(x)'):
        f_t = eqt[eqt.find('=') + 1:].replace('x', 't')
        return f_t
    else:
        return None


path = '/home/mcwave/code/automath/calculus/datasets/function_evaluation/123.txt'
f_x = parse_function_evaluation(path)
print(f_x)

-\tan (8 t)


In [3]:
# import os
# import pickle

# directory = '/home/mcwave/code/automath/calculus/datasets/parametric_equations/'
# files = os.listdir(directory)

# json_path = '/home/mcwave/code/automath/calculus/datasets/parametric_equations.json'
# pickle_path = '/home/mcwave/code/automath/calculus/datasets/parametric_equations.pkl'

# processed_files = set()
# fin = open(json_path, 'r')
# lines = fin.readlines()
# for line in lines:
#     parsed = json.loads(line)
#     processed_files.add(parsed["filename"])

# fin.close()
# print(len(processed_files), "already processed")
    
# fout = open(json_path, 'a')
# pickleout = open(pickle_path, 'ab')

# for file in files:
#     if file in processed_files:
#         print(file, "processed")
#         continue
#     if file.endswith(".txt"):
#         print(file)
#         path = os.path.join(directory, file)
#         f_t, g_t, g_f_t = parse_parametric_equations(path)
#         parsed = {'f_t':f_t, 'g_t':g_t, 'g_f_t':g_f_t}
#         output = {"filename":file}
#         outputs = {"filename":file}
#         for k, v in parsed.items():
#             sbl, expr = convertToSympyWithRetry(v)
#             if sbl is None or expr is None:
#                 continue
#             output[k] = (sbl, expr)
#             outputs[k] = (str(sbl),str(expr))
#         if len(output) > 1:
#             pickle.dump(output, pickleout)
#             pickleout.flush()
#             fout.write(json.dumps(outputs) + '\n')
#             fout.flush()

# fout.close()
# pickleout.close()

In [4]:
import os
import pickle

directory = '/home/mcwave/code/automath/calculus/datasets/function_evaluation/'
files = os.listdir(directory)

json_path = '/home/mcwave/code/automath/calculus/datasets/function_evaluation.json'
pickle_path = '/home/mcwave/code/automath/calculus/datasets/function_evaluation.pkl'

processed_files = set()
fin = open(json_path, 'r')
lines = fin.readlines()
for line in lines:
    parsed = json.loads(line)
    processed_files.add(parsed["filename"])

fin.close()
print(len(processed_files), "already processed")
    
fout = open(json_path, 'a')
pickleout = open(pickle_path, 'ab')

for file in files:
    if file in processed_files:
        print(file, "processed")
        continue
    if file.endswith(".txt"):
        print(file)
        path = os.path.join(directory, file)
        f_t = parse_function_evaluation(path)
        print(f_t)
        parsed = {'f_t':f_t}
        output = {"filename":file}
        outputs = {"filename":file}
        for k, v in parsed.items():
            sbl, expr = convertToSympyWithRetry(v)
            print(sbl, expr)
            if sbl is None or expr is None:
                continue
            output[k] = (sbl, expr)
            outputs[k] = (str(sbl),str(expr))
        if len(output) >= 1:
            try:
                pickle.dump(output, pickleout)
                pickleout.flush()
            except:
                pass
            fout.write(json.dumps(outputs) + '\n')
            fout.flush()

fout.close()
pickleout.close()

15867 already processed
11508.txt processed
7233.txt processed
23916.txt processed
4800.txt processed
29016.txt processed
26545.txt processed
25547.txt processed
21753.txt processed
8423.txt processed
25394.txt processed
43598.txt processed
18293.txt processed
3369.txt processed
23846.txt processed
30686.txt processed
15884.txt processed
43930.txt processed
45690.txt processed
13452.txt processed
23739.txt processed
47013.txt processed
14360.txt processed
22020.txt processed
29318.txt processed
29226.txt processed
5889.txt processed
18603.txt processed
29527.txt processed
48835.txt processed
22324.txt processed
22970.txt processed
44459.txt processed
34711.txt processed
29094.txt processed
30092.txt processed
36494.txt processed
13291.txt processed
1005.txt processed
37251.txt processed
15461.txt processed
24014.txt processed
35257.txt processed
1470.txt processed
595.txt processed
46780.txt processed
45007.txt processed
42931.txt processed
37989.txt processed
21839.txt processed
44140

cos(5)
None None
19125.txt processed
43532.txt processed
24718.txt processed
7540.txt processed
35427.txt processed
45528.txt processed
23029.txt processed
1460.txt processed
26780.txt processed
6198.txt processed
38357.txt processed
221.txt processed
9006.txt processed
25468.txt processed
6727.txt processed
45551.txt processed
2245.txt processed
31035.txt processed
31233.txt processed
37916.txt processed
24692.txt processed
35461.txt processed
6873.txt processed
8135.txt processed
7593.txt
e^6
exp(6)
None None
48940.txt processed
26704.txt processed
33197.txt processed
32431.txt processed
11445.txt processed
14418.txt processed
30895.txt processed
40087.txt processed
37460.txt processed
28652.txt processed
39365.txt processed
49720.txt processed
21570.txt processed
19448.txt processed
30550.txt processed
1244.txt processed
47556.txt processed
4013.txt processed
21669.txt processed
903.txt processed
6570.txt processed
9178.txt processed
11822.txt processed
31041.txt processed
30820.txt

-tan(2)
-tan(2)
None None
34260.txt processed
25196.txt processed
12599.txt processed
37480.txt processed
7496.txt processed
38342.txt processed
12520.txt processed
34478.txt
1
None None
1877.txt processed
23974.txt processed
4315.txt processed
15523.txt processed
33676.txt processed
34672.txt processed
49277.txt
1
1
1
1
None None
11401.txt processed
9519.txt processed
20949.txt processed
22279.txt processed
39650.txt processed
23094.txt processed
5423.txt processed
33141.txt processed
9003.txt processed
18639.txt processed
49175.txt processed
23181.txt processed
40494.txt processed
21220.txt processed
47311.txt processed
13497.txt processed
10830.txt processed
48175.txt processed
21765.txt processed
8134.txt processed
7678.txt processed
26071.txt processed
15737.txt processed
35469.txt processed
2087.txt processed
24358.txt processed
42918.txt processed
21793.txt
1
1
x
1
None None
30034.txt processed
41377.txt
\frac{1}{e^3}
exp(-3)
exp(-3)
None None
3075.txt processed
46415.txt proces

-sin(2)
None None
6913.txt processed
26453.txt processed
28169.txt processed
3141.txt processed
7659.txt
\sqrt{-\sin (6)}
sqrt(-sin(6))
None None
33310.txt processed
9094.txt
\tan ^{-1}(\cos (3))
atan(cos(3))
atan(cos(3))
None None
703.txt processed
21155.txt processed
48897.txt processed
20665.txt processed
37907.txt processed
7076.txt processed
37534.txt processed
44420.txt processed
21686.txt
1
1
Eq(x, 1)
1
None None
32596.txt processed
42973.txt processed
44247.txt processed
18103.txt processed
1114.txt processed
18413.txt processed
26887.txt processed
26616.txt
\log (4)
log(4)
log(4)
log(4)
None None
18186.txt processed
10621.txt processed
42770.txt processed
16169.txt processed
4735.txt processed
12912.txt processed
12093.txt processed
5382.txt processed
44214.txt processed
49429.txt processed
44173.txt processed
26029.txt processed
26561.txt processed
35170.txt processed
9280.txt processed
33245.txt processed
13529.txt processed
6161.txt processed
22609.txt processed
30166.txt p

(-sin(6))**(1/3)
(-sin(6))**0.333333333333333
None None
15360.txt processed
13156.txt processed
46335.txt processed
37078.txt processed
29547.txt processed
29469.txt processed
3442.txt processed
24160.txt processed
471.txt processed
30112.txt processed
40423.txt processed
3575.txt processed
6228.txt processed
36514.txt processed
27196.txt processed
27812.txt processed
4582.txt processed
42592.txt processed
24723.txt processed
21279.txt processed
13395.txt processed
32212.txt processed
27621.txt processed
12165.txt processed
41297.txt processed
46611.txt processed
10145.txt processed
32985.txt processed
14324.txt processed
3005.txt processed
27613.txt processed
47257.txt processed
3087.txt processed
6742.txt processed
13207.txt processed
38295.txt processed
43520.txt processed
8869.txt
\cos (2)
None None
7712.txt processed
7025.txt processed
18509.txt processed
9687.txt processed
35191.txt processed
27064.txt
1
1
1
None None
35990.txt processed
34748.txt processed
47577.txt processed
44

...

cos(4*t + 3)
t cos(4*t + 3)
3912.txt
\sin (\cos (5 t+2))-\tan (3 t+6)
t sin(cos(5*t + 2)) - tan(3*t + 6)
30829.txt
\cos (6 t+3)
t cos(6*t + 3)
25548.txt
\sqrt[3]{3 t+4}+\sqrt[3]{7 t-2}
3**(1/(3*t + 4)) + 3**(1/(7*t - 2))
t 3**(1/(3*t + 4)) + 3**(1/(7*t - 2))
11292.txt
\tan \left(9-\frac{17 t^5}{2}\right) \cot \left(\frac{13 t}{2}+1\right)
t -tan(17*t**5/2 - 9)*cot(13*t/2 + 1)
37119.txt
-\tan \left(\frac{36 t}{5}+\frac{33}{5}\right)
t -tan(36*t/5 + 6.6)
22802.txt
\cos \left(\frac{23}{3}-5 t\right)
t cos(5*t - 7.66666666666667)
32146.txt
-\tan \left(7-\frac{14 t}{3}\right)
t tan(14*t/3 - 7)
40611.txt
e^{8 t-\frac{9}{2}} \cot \left(\frac{17}{2}-\frac{7 t}{2}\right)
t -0.0111089965382423*exp(8*t)*cot(7*t/2 - 8.5)
34526.txt
\tan (3 t+9)
t tan(3*t + 9)
46682.txt
\sqrt[3]{3 t^2+3} (-\csc (3-4 t))
t sqrt(3*t**2 + 3)*csc(4*t - 3)
21234.txt
e^{\frac{3 t}{2}-7}
t exp(3*t/2 - 7)
21101.txt
\sin (8 t) \sin \left(1-6 t^4\right)
t -sin(8*t)*sin(6*t**4 - 1)
48972.txt
\sqrt{-5 t-4}
sqrt(-5*t - 4)
t sqrt

t log(8 - 7*t) - sin(t - 1)
32734.txt
\sin \left(4-5 t^3\right)
t -sin(5*t**3 - 4)
19890.txt
\sqrt{-2 t-4}
t sqrt(-2*t - 4)
19119.txt
\sin (2 t+3)
sin(2*t + 3)
t sin(2*t + 3)
41698.txt
e^{3 t-7}
t exp(3*t - 7)
46651.txt
\frac{\log \left(\frac{10}{3}-\frac{5 t}{3}\right)}{\left(7-\frac{20 t}{3}\right)^4}
t log((3.33333333333333 - 5*t/3)/(7 - 20*t/3)**4)
24844.txt
e^{\frac{7 t^4}{2}+\frac{1}{2}}-\cos \left(\frac{17}{2}-\frac{5 t}{2}\right)
t 1.64872127070013*exp(7*t**4/2) - cos(5*t/2 - 8.5)
32661.txt
\tan \left(3 t^3+1\right)-\frac{1}{(-3 t-8)^5}
tan(3*t**3 + 1) - 1/(-3*t - 8)**5
t tan(3*t**3 + 1) - 1/(-3*t - 8)**5
14198.txt
\frac{\cot (4-2 t)}{\left(4-8 t^2\right)^4}
t -cot(2*t - 4)/(4 - 8*t**2)**4
20396.txt
\log (8)-\sqrt[3]{2 t^2-7}
t -(2*t**2 - 7)**0.166666666666667 + log(8)
41374.txt
\sqrt{6-t}
t sqrt(6 - t)
21714.txt
\sqrt{6} \sqrt{-t}
sqrt(6)*sqrt(-t)
t sqrt(6)*sqrt(-t)
29416.txt
e^{26/3}
5806.11334631499
None None
28145.txt
\frac{1}{-2 t^2-5}
1/(-2*t**2 - 5)
t 1/(-2*t**2 - 5)
420

-(8*t + 8)**0.333333333333333 + 1/(6 - t)
t -(8*t + 8)**0.333333333333333 + 1/(6 - t)
16353.txt
-\tan (3-6 t)
tan(6*t - 3)
t tan(6*t - 3)
21574.txt
-\sin (8-9 t) \tan (t+5)
t sin(9*t - 8)*tan(t + 5)
33674.txt
\log \left(\sqrt[3]{2 t-8}\right)
t log((2*t - 8)**(1/3))
31569.txt
\cos (3 t+8)
cos(3*t + 8)
t cos(3*t + 8)
19646.txt
\sqrt[3]{8 t+9}-\tan (4)
t (8*t + 9)**(1/3) - tan(4)
14705.txt
\tan (8 t+1)
t tan(8*t + 1)
42534.txt
-\tan (t+7)
t -tan(t + 7)
6322.txt
\cot (3 t+4) \sinh ^{-1}(2 t+3)
t cot(3*t + 4)*asinh(2*t + 3)
48283.txt
\cos (4 t+1)
t cos(4*t + 1)
47151.txt
\frac{1}{\left(3 t^3+4\right)^4}
(3*t**3 + 4)**(-4)
t (3*t**3 + 4)**(-4)
9806.txt
\sqrt[3]{-t^2-9}
(-t**2 - 9)**0.333333333333333
t (-t**2 - 9)**0.333333333333333
16211.txt
\sqrt{-2 t-2}
sqrt(-2*t - 2)
t sqrt(-2*t - 2)
44399.txt
\cos (6-6 t)
t cos(6*t - 6)
33137.txt
-\tan ^{-1}\left(4-5 t^2\right)
t atan(5*t**2 - 4)
46951.txt
\cos (6 t+2)
t cos(6*t + 2)
49461.txt
e^{2 t+\frac{7}{3}}
t 10.3122585013258*exp(2*t)
7570.txt
-\c

t cos(7*t - 1)
9966.txt
-\tan ^{-1}(9 t+6)
t -atan(9*t + 6)
35507.txt
\tan \left(8 t^3+2\right)
t tan(8*t**3 + 2)
4667.txt
\frac{\tan \left(6 t^2+5\right)}{\sqrt[3]{7 t+4}}
t tan(6*t**2 + 5)/(7*t + 4)**0.333333333333333
25082.txt
-\tan (3-3 t)
t tan(3*t - 3)
8050.txt
\sqrt[4]{\frac{16 t}{3}-\frac{13}{3}}
t 2*3**(3/4)*(t - 0.8125)**(1/4)/3
16024.txt
-t-1
-t - 1
t -t - 1
9795.txt
e^{2-7 t^2}
t exp(2 - 7*t**2)
28002.txt
\cos \left(5-2 t^2\right)+\tan (5-2 t)
t cos(2*t**2 - 5) - tan(2*t - 5)
18591.txt
\cosh \left(\sqrt{-9 t-8}\right)
cosh(sqrt(-9*t - 8))
t cosh(sqrt(-9*t - 8))
35368.txt
-\sin (3-7 t)
t sin(7*t - 3)
47123.txt
\sqrt{9-4 t}
sqrt(9 - 4*t)
t sqrt(9 - 4*t)
40077.txt
\tan ^{-1}(5 t+1)-\sqrt[3]{-7 t-3}
-(-7*t - 3)**0.333333333333333 + tan(5*t + 1)
t -(-7*t - 3)**0.333333333333333 + tan(5*t + 1)
17874.txt
\sqrt[3]{4 t^2+5}-\log (9-5 t)
(4*t**2 + 5)**0.333333333333333 - log(9 - 5*t)
t (4*t**2 + 5)**0.333333333333333 - log(9 - 5*t)
27266.txt
\log \left(\frac{11}{3}-3 t\right)-\sin \l

1/(4096*(t + 1)**4)
t (8*t + 8)**(-4)
12839.txt
\log (4 t-2)-\sqrt[3]{t^4+3}
-(t**4 + 3)**0.333333333333333 + log(4*t - 2)
t -(t**4 + 3)**0.333333333333333 + log(4*t - 2)
39969.txt
-\sin (7 t+4)
t -sin(7*t + 4)
22967.txt
\sqrt[3]{3 t+5}
(3*t + 5)**(1/3)
t (3*t + 5)**(1/3)
11605.txt
\cos (2 t+4)
cos(2*t + 4)
t cos(2*t + 4)
26958.txt
-\tan \left(2 t^5\right)
t -tan(2*t**5)
7957.txt
-\tan (4 t+8)
-tan(4*t + 8)
t -tan(4*t + 8)
31897.txt
-\sin (2-6 t) \sin \left(3 t^2+2\right)
t sin(6*t - 2)*sin(3*t**2 + 2)
40063.txt
\sqrt[3]{t^3+6}
(t**3 + 6)**(1/3)
t (t**3 + 6)**(1/3)
19990.txt
\frac{1}{\left(\frac{8 t}{5}+\frac{8}{5}\right)^2}
t 0.390625/(1.0*t + 1)**2
3104.txt
e^{-6 t-4}
t exp(-6*t - 4)
14869.txt
\cos (8 t+8)
t cos(8*t + 8)
46803.txt
-\sqrt[3]{\frac{11}{5}-\frac{13 t}{5}}-\sin \left(\frac{19}{5}-2 t\right)
t -1.17263330460726*(0.846153846153846 - t)**0.166666666666667 + sin(2*t - 3.8)
32261.txt
\sin \left(2-8 t^2\right)+\cos (t+4)
t -sin(8*t**2 - 2) + cos(t + 4)
38279.txt
-\frac{\sin (6